# Using BioPython Blast implimentation

Simply exploring the components provided by BioPython. We need to:
1. Blast all organism 16s rRNA vs eachother
2. Blast all proteins in meso-thermo pairs

In [1]:
import pandas as pd
import ast
from Bio import SeqIO, SeqRecord, Seq
import tempfile
import os

from Bio.Blast.Applications import NcbiblastnCommandline
from Bio.Blast import NCBIXML

Load a sample of some 16s:

In [2]:
seq_table = pd.read_csv('../data/taxa/16s_rRNA.csv', index_col=0, nrows=200)['seq_16srRNA'].apply(lambda s: s if s != 'None' else None).dropna()

SeqIO Expets TAB seperated values... dumb. Save as fasta in tmp file

In [3]:
query_temp = tempfile.NamedTemporaryFile('w', delete=False)
query_temp.close()
db_temp = tempfile.NamedTemporaryFile('w', delete=False)
db_temp.close()
out_temp = tempfile.NamedTemporaryFile('w', delete=False)
out_temp.close()
records = [SeqRecord.SeqRecord(Seq.Seq(str(seq_str)), id=str(id_)) for id_, seq_str in seq_table.items()]
with open(query_temp.name, 'wt') as f:
    SeqIO.write(records[:5], f, 'fasta')
with open(db_temp.name, 'wt') as f:
    SeqIO.write(records[5:], f, 'fasta')

NcbiblastnCommandline(query=query_temp.name, subject=db_temp.name, outfmt=5, out=out_temp.name)()
f = open(out_temp.name, 'r')
blast_result_record = NCBIXML.parse(f)

In [4]:
with open(query_temp.name, 'r') as file:
    print(file.readlines())
print('---------------------')
with open(db_temp.name, 'r') as file:
    print(file.readlines())
print('---------------------')
with open(out_temp.name, 'r') as file:
    print(file.readlines())
print('---------------------')

['>0 <unknown description>\n', 'ACGATGGAGAGTTTGATCCTGGCTCAGGATGAACGCTAGCGGCAGGCCTAATACATGCAA\n', 'GTCGAGCGGGCCGCAAGGT\n', '>1 <unknown description>\n', 'TCAACGGAGAGTTTGATCCTGGCTCAGGACGAACGCTGGCGGCGTGCTTAACACATGCAA\n', 'GTCGAGCGGTAAGGCCCTTCGGGGTACACGAGCGGCGAACGGGTGAGTAACACGTGGGTG\n', 'ATCTGCCCTGCACTTCGGGATAAGCCTGGGAAACTGGGTCTAATACCGGATATGACCTTC\n', 'GGCTGCATGGCCGAGGGTGGAAAGGTTTACTGGTGCAGGATGGGCCCGCGGCCTATCAGC\n', 'TTGTTGGTGGGGTAATGGCCTACCAAGGCGACGACGGGTAGCCGACCTGAGAGGGTGACC\n', 'GGCCACACTGGGACTGAGACACGGCCCAGACTCCTACGGGAGGCAGCAGTGGGGAATATT\n', 'GCACAATGGGCGAAAGCCTGATGCAGCGACGCCGCGTGAGGGATGACGGCCTTCGGGTTG\n', 'TAAACCTCTTTCAGCAGGGACGAAGCGAAAGTGACGGTACCTGCAGAAGAAGCACCGGCT\n', 'AACTACGTGCCAGCAGCCGCGGTAATACGTAGGGTGCAAGCGTTGTCCGGAATTACTGGG\n', 'CGTAAAGAGTTCGTAGGCGGTTTGTCGCGTCGTTTGTGAAAACTCACAGCTCAACTGTGA\n', 'GCCTGCAGGCGATACGGGCAGACTTGAGTACTGCAGGGGAGACTGGAATTCCTGGTGTAG\n', 'CGGTGAAATGCGCAGATATCAGGAGGAACACCGGTGGCGAAGGCGGGTCTCTGGGCAGTA\n', 'ACTGACGCTGAGGAACGAAAGCGTGGGTAGCAAACAGGATTAGATACCCTGGTAG

In [5]:
record = next(blast_result_record)

record attributes

In [6]:
dir(record)

['__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 'alignments',
 'application',
 'blast_cutoff',
 'database',
 'database_length',
 'database_letters',
 'database_name',
 'database_sequences',
 'date',
 'descriptions',
 'dropoff_1st_pass',
 'effective_database_length',
 'effective_hsp_length',
 'effective_query_length',
 'effective_search_space',
 'effective_search_space_used',
 'expect',
 'filter',
 'frameshift',
 'gap_penalties',
 'gap_trigger',
 'gap_x_dropoff',
 'gap_x_dropoff_final',
 'gapped',
 'hsps_gapped',
 'hsps_no_gap',
 'hsps_prelim_gapped',
 'hsps_prelim_gapped_attemped',
 'ka_params',
 'ka_params_gap',
 'matrix',
 'multiple_alignment',
 'num_good_extends',
 

In [7]:
record.blast_cutoff

(None, None)

In [8]:
record.query

'0 <unknown description>'

In [42]:
record.query_length

1519

nothing else returns anything

In [9]:
record.alignments

In [10]:
alignment = record.alignments[0]

alignment attributes

In [11]:
dir(alignment)

['__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 'accession',
 'hit_def',
 'hit_id',
 'hsps',
 'length',
 'title']

In [12]:
alignment.hit_id

'65'

In [13]:
alignment.hit_def

'65 <unknown description>'

In [15]:
for hsp in alignment.hsps:
    print('Score: ', hsp.score)
    print('E: ', hsp.expect)
    print('N gaps: ', hsp.gaps)
    print('N aligns: ', hsp.num_alignments)
    print('Identities: ', hsp.identities)
    for i in range(len(hsp.query)//75):
        print(hsp.query[i*75:(i+1)*75])
        print(hsp.match[i*75:(i+1)*75])
        print(hsp.sbjct[i*75:(i+1)*75])
    print(hsp.query[(i+1)*75:])
    print(hsp.match[(i+1)*75:])
    print(hsp.sbjct[(i+1)*75:])
    print('--------------------------------------')

Score:  66.0
E:  1.3754e-30
N gaps:  0
N aligns:  None
Identities:  68


NameError: name 'i' is not defined

Let's try to create an output table by taking the best HSP for each "hit" eg the best local alignment for each match

In [24]:
import numpy as np
import re

In [37]:
f = open(out_temp.name, 'r')
blast_result_record = NCBIXML.parse(f)

In [38]:
pairs = []
for record in blast_result_record:
    print('########################')
    print('Query ', record.query.split(' ')[0])
    print('-------------------------')
    for alignment in record.alignments:
        print('>>>>>> Hit ', alignment.hit_id)
        print(f"Hit seq len: {len(seq_table.loc[int(alignment.hit_id)])}")
        print('Hit Length: ', alignment.length)
        scores = []
        for hsp in alignment.hsps:
            if hsp.gaps > 1 or True:
                print('\tScore: ', hsp.score)
                print('\tE: ', hsp.expect)
                print('\tN gaps: ', hsp.gaps)
                print('\tN compressed gaps: ', len(re.findall('-+', hsp.query))+len(re.findall('-+', hsp.sbjct)))
                print('\tIdentities: ', hsp.identities)
                print('\tLen query, subject, match: ', (len(hsp.query), len(hsp.sbjct), len(hsp.match)))
                for i in range(len(hsp.query)//150+1):
                    print('\t', hsp.query[i*150:(i+1)*150])
                    print('\t', hsp.match[i*150:(i+1)*150])
                    print('\t', hsp.sbjct[i*150:(i+1)*150])
                print('\t------------------------')

            scores.append(hsp.expect)
        print('HSP scores ', scores)
        if len(scores) > 0:
            pairs.append((record.query.split(' ')[0], alignment.hit_id, np.log(min(scores))))

########################
Query  0
-------------------------
>>>>>> Hit  65
Hit seq len: 1524
Hit Length:  1524
	Score:  66.0
	E:  1.3754e-30
	N gaps:  0
	N compressed gaps:  0
	Identities:  68
	Len query, subject, match:  (69, 69, 69)
	 ACGATGGAGAGTTTGATCCTGGCTCAGGATGAACGCTAGCGGCAGGCCTAATACATGCAAGTCGAGCGG
	 || ||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||
	 ACAATGGAGAGTTTGATCCTGGCTCAGGATGAACGCTAGCGGCAGGCCTAATACATGCAAGTCGAGCGG
	------------------------
HSP scores  [1.3754e-30]
>>>>>> Hit  181
Hit seq len: 1522
Hit Length:  1522
	Score:  63.0
	E:  6.3991e-29
	N gaps:  0
	N compressed gaps:  0
	Identities:  67
	Len query, subject, match:  (69, 69, 69)
	 ACGATGGAGAGTTTGATCCTGGCTCAGGATGAACGCTAGCGGCAGGCCTAATACATGCAAGTCGAGCGG
	 || |||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||| |||
	 ACAATGGAGAGTTTGATCCTGGCTCAGGATGAACGCTAGCGGCAGGCCTAATACATGCAAGTCGAACGG
	------------------------
HSP scores  [6.3991e-29]
>>>>>> Hit  163
Hit seq len: 1456
Hit Length:  1456
	Sc

/var/folders/9j/1f7mt18d2pqcwws6hwdx7_kr0000gn/T/ipykernel_9832/1809482981.py:28: RuntimeWarning: divide by zero encountered in log
  pairs.append((record.query.split(' ')[0], alignment.hit_id, np.log(min(scores))))


In [17]:
os.remove(query_temp.name)
os.remove(db_temp.name)
os.remove(out_temp.name)

In [11]:
blast_df = pd.DataFrame(data=pairs, columns=['query', 'hit', 'E'])

In [14]:
pivot = blast_df.pivot(index='query', columns='hit', values='E')
pivot

hit    100  101  102  103  104  105  106  107  108         109  ...   90  \
query                                                           ...        
0      NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  -61.078811  ...  NaN   
1     -inf -inf -inf -inf -inf -inf -inf -inf -inf -404.793389  ... -inf   
2     -inf -inf -inf -inf -inf -inf -inf -inf -inf        -inf  ... -inf   
3     -inf -inf -inf -inf -inf -inf -inf -inf -inf        -inf  ... -inf   
4     -inf -inf -inf -inf -inf -inf -inf -inf -inf        -inf  ... -inf   

hit            91          92   93          94   95          96          97  \
query                                                                         
0      -48.278808         NaN  NaN  -59.798806  NaN         NaN  -45.718807   
1             NaN -112.953392 -inf -359.993393 -inf  -88.633393 -343.353392   
2      -56.652943 -101.452942 -inf        -inf -inf -112.972941 -342.092942   
3             NaN -119.352727 -inf -344.632727 -inf  -80.952724 -285.752724   
4     -109.098812 -105.258812 -inf -325.418812 -inf         NaN -411.178812   

hit           98   99  
query                  
0     -63.638813  NaN  
1           -inf -inf  
2           -inf -inf  
3           -inf -inf  
4           -inf -inf  

[5 rows x 186 columns]

E values for many pairings were 0, meaning for the sequence length and "database" size, the match is significant. I expect these E values to go up as the database size increases, however if they do not it will be difficult to resolve small differences. Let's try just a 1v1

In [18]:
query_temp = tempfile.NamedTemporaryFile('w', delete=False)
query_temp.close()
db_temp = tempfile.NamedTemporaryFile('w', delete=False)
db_temp.close()
out_temp = tempfile.NamedTemporaryFile('w', delete=False)
out_temp.close()
records = [SeqRecord.SeqRecord(Seq.Seq(str(seq_str)), id=str(id_)) for id_, seq_str in seq_table.items()]
with open(query_temp.name, 'wt') as f:
    SeqIO.write([records[3]], f, 'fasta')
with open(db_temp.name, 'wt') as f:
    SeqIO.write([records[104]], f, 'fasta')

NcbiblastnCommandline(query=query_temp.name, subject=db_temp.name, outfmt=5, out=out_temp.name)()
f = open(out_temp.name, 'r')
blast_result_record = NCBIXML.parse(f)

In [19]:
pairs = []
for record in blast_result_record:
    print('########################')
    print('Query ', record.query.split(' ')[0])
    print('-------------------------')
    for alignment in record.alignments:
        print('>>>>>> Hit ', alignment.hit_id)
        print('Length: ', alignment.length)
        scores = []
        for hsp in alignment.hsps:
            print('\tScore: ', hsp.score)
            print('\tE: ', hsp.expect)
            print('\tN gaps: ', hsp.gaps)
            print('\tIdentities: ', hsp.identities)
            for i in range(len(hsp.query)//150+1):
                print('\t', hsp.query[i*150:(i+1)*150])
                print('\t', hsp.match[i*150:(i+1)*150])
                print('\t', hsp.sbjct[i*150:(i+1)*150])
            print('\t------------------------')

            scores.append(hsp.expect)
        print('HSP scores ', scores)
        if len(scores) > 0:
            pairs.append((record.query.split(' ')[0], alignment.hit_id, np.log(min(scores))))

########################
Query  4
-------------------------
>>>>>> Hit  106
Length:  1524
	Score:  497.0
	E:  0.0
	N gaps:  76
	Identities:  1223
	 ATGGAGAGTTTGATCCTGGCTCAGGATGAACGCTGGCGGCATGCCTAATACATGCAAGTCGAACGAAGTTTTTAGGAAAGCTTGCTTTCCAAAAAGACTTAGTGGCGAACGGGTGAGTAACACGTAGA-TAACCTGCCCATGTGCCCGGG
	 |||||||||||||||||||||||||| ||||||||||||| ||| ||| |||||||||||||||||  |  |  ||   ||||||   ||     || ||||||||||||||||||||||||||| || |||||||||| ||    ||||
	 ATGGAGAGTTTGATCCTGGCTCAGGACGAACGCTGGCGGCGTGCTTAACACATGCAAGTCGAACGA--TGATGCGG--TGCTTGC--ACC--GTGGA-TTAGTGGCGAACGGGTGAGTAACACGT-GAGTAACCTGCCCCTGACTTCGGG
	 ATAACTGCT-GGAAACGGTAGCTAAAACCGGATAGGTGGCTT-C-GAGGCATCTCGGAGACATTAAAATGGCTAAGGCCATGAACATGGAT-GGATCTGCGGCGCATTAGCTAGTTGGTGAGGTAACGGCCCACCAAGGCGACGATGCGT
	 ||||   || |||||| |   |||| ||||||||  || ||| | |  ||||   || |     ||| |   |  ||   ||     |||| || || |||||  || |||| ||||||| ||| | |||| ||||||||||||| | ||
	 ATAA-GCCTGGGAAACTGGGTCTAATACCGGATA--TGACTTCCTGCCGCATGGTGGGGGGTGGAAAGT-TTTTCGG--TTG----G

/var/folders/9j/1f7mt18d2pqcwws6hwdx7_kr0000gn/T/ipykernel_92313/4209320813.py:24: RuntimeWarning: divide by zero encountered in log
  pairs.append((record.query.split(' ')[0], alignment.hit_id, np.log(min(scores))))


In [20]:
os.remove(query_temp.name)
os.remove(db_temp.name)
os.remove(out_temp.name)

The score is still 0. 

### Current conclusion
What we get back from biopython blast does not return global statistics, only untiled HSPs

As an approximation, we can take the "best" (most query matches) HSP and "scale it up" using query and subject sequence length.
The metric we use will be a parameter. For now, I am unable to compute global percent identity so will move foward with the above approximation.